# TP8 : Calculs de distance
Le but de ce TP est de vous remettre dans le bain de `python` et de préparer le TP suivant. Nous allons calculer des distances dans diverses circonstances.

## Exercices 1 : distance enclidenne entre deux points
On se place dans l'hyperespace ${\mathbb R}^n$ de dimension $n$. La _distance euclidienne_ entre deux points $x=(x_1,\dots ,x_n)$ et $y=(y_1,\dots, y_n)$ est donnée par

$$\sqrt{\sum\limits_{k=1}^n (y_k-x_k)^2}\:.$$

On suppose qu'un point est donné par la liste de ses coordonnées. Écrire une fonction `distance_euclidienne_points` qui prend en argument deux points de même dimension et renvoie leur distance.

In [14]:
import math

def distance_euclidienne_points(x, y):
    """x et y sont des listes de nombres de même longueur"""
    assert(len(x) == len(y))
    return math.sqrt(sum([(y[k] - x[k])**2 for k in range(len(x))]))

In [15]:
import math
epsilon = 0.000001
assert(math.fabs(distance_euclidienne_points([0], [1]) - 1) < epsilon)
assert(math.fabs(distance_euclidienne_points([1,2,3], [1,2,3])) < epsilon)
assert(math.fabs(distance_euclidienne_points([1,2,3,4,5], [9,8,7,6,5]) - 10.954451150103322) < epsilon)

## Interlude : conversion entre un tableau de niveau de gris et une image
Dans la suite, on va travailler sur des images. Quand on aura une image, on commencera par la convertir en noir et blanc (ie en niveaux de gris), puis on produira une liste de listes contenant les niveaux de gris.

Pour cela, nous allons utiliser la fonction suivante :

In [16]:
from PIL import Image

def img2array(fic):
    """fic est le nom d'un fichier contenant une image
    la fonction renvoie une liste de listes d'entiers représentants des niveaux de gris"""
    im = Image.open(fic).convert('L')  ## chargement et passage en niveaux de gris
    tab = []
    i = 0
    for c in im.getdata():
        if i % im.width == 0: ## debut d'une nouvelle ligne dans l'image
            tab.append([])
        tab[-1].append(c)
        i += 1
    im.close()
    return tab

In [17]:
t = img2array('image.jpeg')

Pour récupérer un fichier image à partir d'une liste de listes de niveaux de gris, vous pouvez utiliser la fonction suivante:

In [18]:
from PIL import Image

def array2img(tab, fic):
    """fic est un nom de fichier avec un extension valide pour une image,
    tab est une liste de listes de niveaux de gris
    la fonction écrit l'image dans le fichier"""
    im = Image.new(size=(len(tab[0]), len(tab)), mode='L')
    for i in range(len(tab)):
        for j in range(len(tab[0])):
            im.putpixel((j, i), tab[i][j])
    im.save(fic)

In [19]:
array2img(t, 'image2.ppm')

In [20]:
t = img2array('image2.ppm')
array2img(t, 'image3.ppm')

## Exercice 2 : distance euclidienne entre deux images
Si on considère une image comme une matrice de points, on peut de la même manière calculer une distance euclidienne entre deux images de même dimension en regardant les distances pixels par pixels.

Écrire une fonction `distance_eclidienne_image` qui prend en arguments deux images (données sous la forme des noms des fichiers les contenant) supposées de même dimension et calcule la distance euclidienne entre ces deux images.

In [21]:
def distance_euclidienne_image(img1, img2):
    im1 = img2array(img1)
    im2 = img2array(img2)
    assert(len(im1) == len(im2) and len(im1[0]) == len(im2[0]))
    return math.sqrt(sum([(im1[i][j] - im2[i][j])**2 for i in range(len(im1)) for j in range(len(im1[0]))]))

In [22]:
distance_euclidienne_image('a.png', 'b.png')

18031.22292025696

In [23]:
distance_euclidienne_image('image2.ppm', 'image3.ppm')

0.0

In [24]:
t1 = img2array('essai.jpeg')
t2 = img2array('essai.png')

In [25]:
def damier(haut, larg, first, C):
    t = []
    couleur_debut_ligne = first
    for _ in range(haut):
        couleur_debut_ligne += 1
        couleur_debut_ligne %= 2
        for _ in range(C):
            couleur_case = couleur_debut_ligne
            t.append([])
            for _ in range(larg):
                couleur_case += 1
                couleur_case %= 2
                for _ in range(C):
                    t[-1].append(couleur_case*255)
    return t

In [26]:
array2img(damier(5, 10, 0, 10), 'a.png')

In [27]:
array2img(damier(5, 10, 1, 10), 'b.png')

In [28]:
array2img(damier(1, 2, 1, 50), 'c.png')

In [29]:
distance_euclidienne_image('a.png', 'b.png')

18031.22292025696

In [30]:
distance_euclidienne_image('b.png', 'c.png')

12492.397688194209

In [31]:
array2img(damier(2, 4, 0, 10), 'a_petit.png')

In [32]:
array2img(damier(2, 4, 1, 10), 'b_petit.png')

In [33]:
array2img(damier(1, 2, 0, 20), 'c_petit.png')

## Exercice 3 : distance de Hausdorf entre deux images
Considérons les trois images suivantes:

(a) : ![](a.png)  (b) : ![](b.png)  (c) : ![](c.png)

La distance euclidienne n'est pas extrêmement satisfaisante car :

In [34]:
distance_euclidienne_image('a.png', 'b.png')

18031.22292025696

In [35]:
distance_euclidienne_image('b.png', 'c.png')

12492.397688194209

alors qu'on a envie de dire de façon intuitive que (a) est plus proche de (b) que (c).

On va considérer une autre distance appelée _distance de Hausdorf_.

L'idée de la distance de Hausdorf entre deux images `img1` et `img2` est de considérer pour chaque point de `img1` la distance (en distance euclidienne des coordonnées) minimale à un point identique de `img2`, et de prendre le maximum de cette valeur sur l'ensemble des points de `img2`. On considère que deux points sont identiques si leurs niveaux de gris respectifs ne diffèrent pas de plus de 10 au sens large.

1. Écrire une fonction `point_identique_le_plus_proche` qui prend en argument deux listes de listes d'entiers représentant deux images `img1` et `img2` en noir et blanc supposées de même dimension, et deux entiers représentant respectivemnt l'abscisse et l'ordonnée d'un point dans `img1` et renvoie les coordonnées du point identique de `img2` le plus proche. 

In [36]:
import math

def distance_au_point_identique_le_plus_proche(tab1, tab2, x, y):
    d = math.inf
    for i in range(len(tab1)):
        for j in range(len(tab1[0])):
            if math.fabs(tab1[x][y] - tab2[i][j]) <= 10:
                dd = distance_euclidienne_points([x, y], [i, j])
                if dd < d:
                    d = dd
    return d

In [37]:
distance_au_point_identique_le_plus_proche(img2array('b_petit.png'), img2array('c_petit.png'), 1, 1)

19.0

2. Écrire une fonction `distance_Hausdorf` qui prend en argument les noms de deux fichiers contenant des images supposées de même taille et renvoie leur distance de Hausdorf.

In [38]:
def distance_Hausdorf(fic1, fic2):
    tab1 = img2array(fic1)
    tab2 = img2array(fic2)
    assert(len(tab1) == len(tab2) and len(tab1[0]) == len(tab2[0]))
    m = 0
    for x in range(len(tab1)):
        for y in range(len(tab1[0])):
            pp = distance_au_point_identique_le_plus_proche(tab1, tab2, x, y)
            if pp > m:
                m = pp
    return m

Pour les tests, la fonction `distance_Hausdorf` ayant une complexité assez mauvaise, nous les ferons sur les images suivantes:

(a) ![](a_petit.png) (b) : ![](b_petit.png) (c) : ![](c_petit.png)

Comparez :

In [39]:
distance_euclidienne_image('a_petit.png', 'b_petit.png')

7212.489168102785

In [40]:
distance_euclidienne_image('b_petit.png', 'c_petit.png')

5100.0

In [41]:
distance_Hausdorf('a_petit.png', 'b_petit.png')

10.0

In [42]:
distance_Hausdorf('b_petit.png', 'c_petit.png')

20.0

Sur cet exemple, la distance de Hausdorf correcpond plus à l'idée qu'on se fait de la distance entre deux images. De même, si une a un peu bougé par rapport à l'original, ou si elle est un peu flou, on trouvera une distance pas trop grande.

http://cgm.cs.mcgill.ca/~godfried/teaching/cg-projects/98/normand/main.html

## Exercice 4 : détection de contours [difficile]
La complexité de la fonction `distance_Hausdorf` est quadratique sur le nombre de pixels de l'image, donc en $O(n^4)$ si $n$ est le côté de l'image quand celle-ci est carrée. Ce qui la rend inutilisable en pratique. Pour diminuer le temps d'exécution, une approche possible est de ne pas faire un calcul pour chaque point de l'image, mais uniquement pour certains points remarquables, par exemple les points qui apparaissent sur les contours.

Le principe pour trouver le contour d'une image, est de repérer les points dont la couleur (ici le niveau de gris) varie particulièrement par rapport aux couleurs des voisins.

Pour cela, on regarde la variation par rapport au voisin du dessous et au voisin de droite (en fait par rapport au voisin obtenu en décrémentant l'abscisse et au voisin obtenu en décrémentant l'ordonnée, peu importe l'orientation de l'image).

1. Écrire une fonction `derivee` qui prend en argument une liste de listes de niveaux de gris `T`, et deux indices 'x' et 'y' qui ne sont pas sur les bords et calcule la dérivée en le point de coordonnées $(x, y)$, c'est-à-dire
$$\sqrt{\bigl(T(x,y)-T(x-1,y)\bigr)^2+\bigl(T(x,y)-T(x,y-1)\bigr)^2}$$

In [43]:
import math

def derivee(tab, x, y):
    assert(x > 0 and y > 0)
    return math.sqrt( (tab[x][y] - tab[x-1][y])**2 + (tab[x][y] - tab[x][y-1])**2 )

In [44]:
derivee([[1,2,3], [9,8,7], [6,13,3]], 1, 1)

6.082762530298219

2. Écrivez une fonction `seuil` qui prend en argument une liste de listes de niveaux de gris `T` et un entier `s` et renvoie une liste `S` de coordonnées telle que $(x, y)$ appartient à cette liste si et seulement si la dérivée de `T` au point $(x, y)$ est définie et supérieure au seuil `s`.

In [45]:
def seuil(tab, s):
    S = [ ]
    for x in range(1, len(tab)):
        for y in range(1, len(tab[0])):
            if derivee(tab, x, y) > s:
                S.append((x,y))
    return S

3. Écrire une fonction `distance_au_point_identique_le_plus_proche_amelioree` qui est une variante de `distance_au_point_identique_le_plus_proche`: en plus des paramètres de `distance_au_point_identique_le_plus_proche`, elle prend en paramètre une liste de coordonnées et ne compare ce qui se passe au point $(x, y)$ qu'avec les points dont les coordonnées appartiennent à cette liste.

In [46]:
def distance_au_point_identique_le_plus_proche_amelioree(tab1, tab2, x, y, contour):
    d = math.inf
    for (i, j) in contour:
        if math.fabs(tab1[x][y] - tab2[i][j]) <= 10:
            dd = distance_euclidienne_points([x, y], [i, j])
            if dd < d:
                d = dd
    return d

4. Écrire une fonction `distance_Hausdorf_amelioree` qui prend en argument les noms de deux fichiers contenant des images supposées de même taille et renvoie la variante de leur distance de Hausdorf qui comparent les points des contours des deux images à partir des listes obtenues par `seuil`.

In [47]:
def distance_Hausdorf_amelioree(fic1, fic2, s):
    tab1 = img2array(fic1)
    tab2 = img2array(fic2)
    assert(len(tab1) == len(tab2) and len(tab1[0]) == len(tab2[0]))
    contour1 = seuil(tab1, s)
    contour2 = seuil(tab2, s)
    m = 0
    for (x, y) in contour1:
        pp = distance_au_point_identique_le_plus_proche_amelioree(tab1, tab2, x, y, contour2)
        if pp > m:
            m = pp
    return m

In [48]:
distance_Hausdorf_amelioree('a_petit.png', 'b_petit.png', 100)

9.055385138137417

In [65]:
t = img2array('a.png')

In [66]:
len(t) * len(t[0])

5000

In [67]:
len(seuil(t, 100))

801

On peut maintenant calculer les distances de Hausdorf améliorées sur les petites images:

In [68]:
distance_Hausdorf_amelioree('b_petit.png', 'c_petit.png', 100)

longueur du contour : 93


14.212670403551895

In [69]:
distance_Hausdorf_amelioree('a.png', 'b.png', 100)

longueur du contour : 801


9.055385138137417

In [70]:
distance_Hausdorf_amelioree('b.png', 'c.png', 100)

longueur du contour : 801


50.0

Mais également sur les plus grandes:

In [71]:
distance_Hausdorf('a.png', 'b.png')

10.0

In [72]:
distance_Hausdorf('b.png', 'c.png')

50.0

In [1]:
from PIL import Image

In [2]:
im = Image.open("image.png")

In [3]:
im.height

755

In [4]:
im.width

592

In [5]:
im.getpixel((13,6))

(255, 255, 255, 255)

In [6]:
im.show()

In [9]:
im2 = im.convert("L")

In [11]:
for i in im2.getdata():
    print(i)

255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255


255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255


255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255


255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
203
0
190
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
196
35
124
211
211
143
31
191
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
211
190
0
203
255
255
255
255
255
255
255
255
255
25

255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
254
0
169
211
211
211
211
211
211
211
211
211
211
211
211
211
211
21

...

211
211
211
211
211
211
148
23
87
254
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
25

211
211
211
211
211
211
211
211
211
211
190
129
66
0
47
145
246
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255


255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255


255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255


255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255
255


In [12]:
im2.getdata()

In [13]:
im2.height

755

In [ ]:
im2.save('toto.jpg')